# Latent space encoding using LSTMs: Finding similar word context

In [1]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

from sklearn.preprocessing import OneHotEncoder
from sklearn.metrics.pairwise import euclidean_distances

import numpy as np
import pandas as pd

In [2]:
maxlen = 3
max_features = 1000

Let's prepare the encoding that the Keras dataloader uses, so we can encode input, and reverse the output:

In [3]:
word_to_id = keras.datasets.imdb.get_word_index()
word_to_id = {k:(v+3) for k,v in word_to_id.items()}
word_to_id["<PAD>"] = 0
word_to_id["<START>"] = 1
word_to_id["<UNK>"] = 2
word_to_id["<UNUSED>"] = 3
id_to_word = {value:key for key,value in word_to_id.items()}

## Get the data

We load the data nad preprocess it so the LSTMs can process it. This also handles the padding, in case a review is shorter than the defined sequence length.

In [4]:
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.imdb.load_data(num_words=max_features)

In [5]:
x_train = keras.preprocessing.sequence.pad_sequences(x_train, maxlen=maxlen)
x_test = keras.preprocessing.sequence.pad_sequences(x_test, maxlen=maxlen)

In [6]:
x_train.shape

(25000, 3)

In [7]:
x_train[0]

array([ 19, 178,  32], dtype=int32)

In [8]:
all = []
for it in range(x_train.shape[0]):
    row = np.zeros((maxlen, max_features))
    for jt in range(maxlen):
        row[jt, x_train[it, jt]] = 1
    all.append(row * 1.0)

In [9]:
data_enc = np.array(all)

In [10]:
data_enc.shape

(25000, 3, 1000)

In [11]:
np.argmax(data_enc[0], axis=1).tolist()

[19, 178, 32]

## Build the model

In [12]:
inputs = keras.Input(shape=(None,), dtype="int32")
x = layers.Embedding(max_features, 128)(inputs)
x = layers.Bidirectional(layers.LSTM(128))(x)
x = layers.BatchNormalization()(x)
encoded = layers.Dense(3)(x)

In [18]:
x = layers.Dense(3)(layers.RepeatVector(maxlen)(encoded))
x = layers.BatchNormalization()(x)
x = layers.Bidirectional(layers.LSTM(128, return_sequences=True))(x)
decoded = layers.TimeDistributed(layers.Dense(max_features))(x)
decoded = layers.Softmax(name="decoded")(decoded)
sentiment = layers.Dense(1)(x[:, -1])
sentiment = layers.Activation('sigmoid', name="sentiment")(sentiment)

In [20]:
model = keras.Model(inputs, [decoded, sentiment])
model.summary()

Model: "functional_7"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, None)]       0                                            
__________________________________________________________________________________________________
embedding (Embedding)           (None, None, 128)    128000      input_1[0][0]                    
__________________________________________________________________________________________________
bidirectional (Bidirectional)   (None, 256)          263168      embedding[0][0]                  
__________________________________________________________________________________________________
batch_normalization (BatchNorma (None, 256)          1024        bidirectional[0][0]              
_______________________________________________________________________________________

In [21]:
encoder = keras.Model(inputs, encoded)
decoder = keras.Model(inputs, decoded)

In [22]:
model.compile(optimizer='adam', loss={'decoded': 'categorical_crossentropy', 'sentiment': 'binary_crossentropy'})

In [23]:
model.fit(x_train, {'decoded': data_enc, 'sentiment': y_train}, epochs=50)

Epoch 1/50
782/782 [==============================] - 7s 9ms/step - loss: 4.8706 - decoded_loss: 4.1762 - sentiment_loss: 0.6944
Epoch 2/50
782/782 [==============================] - 7s 9ms/step - loss: 4.2768 - decoded_loss: 3.5827 - sentiment_loss: 0.6940
Epoch 3/50
782/782 [==============================] - 7s 9ms/step - loss: 3.9768 - decoded_loss: 3.2835 - sentiment_loss: 0.6933
Epoch 4/50
782/782 [==============================] - 7s 9ms/step - loss: 3.7059 - decoded_loss: 3.0140 - sentiment_loss: 0.6919
Epoch 5/50
782/782 [==============================] - 8s 10ms/step - loss: 3.5577 - decoded_loss: 2.8696 - sentiment_loss: 0.6881
Epoch 6/50
782/782 [==============================] - 8s 10ms/step - loss: 3.4557 - decoded_loss: 2.7705 - sentiment_loss: 0.6852
Epoch 7/50
782/782 [==============================] - 8s 10ms/step - loss: 3.3726 - decoded_loss: 2.6928 - sentiment_loss: 0.6798
Epoch 8/50
782/782 [==============================] - 8s 11ms/step - loss: 3.3032 - decoded_lo

In [27]:
res = model.predict(x_test)

In [29]:
res[0].shape, res[1].shape

((25000, 3, 1000), (25000, 1))

## Diplaying the latent space

In [32]:
import plotly.graph_objects as go

In [33]:
enc = encoder.predict(x_train)

In [34]:
enc[0]

array([ 7.3765574,  2.6015177, -4.1122513], dtype=float32)

### Display by sentiment

In [35]:
plot_data = [[], []]

In [36]:
for it in range(y_train.shape[0]):
    plot_data[y_train[it]].append(enc[it])

In [63]:
fig = go.Figure([
    go.Scatter3d(
        x=np.array(plot_data[0])[:, 0],
        y=np.array(plot_data[0])[:, 1],
        z=np.array(plot_data[0])[:, 2],
        mode='markers',
        marker={'size': 1},
    ),
    go.Scatter3d(
        x=np.array(plot_data[1])[:, 0],
        y=np.array(plot_data[1])[:, 1],
        z=np.array(plot_data[1])[:, 2],
        mode='markers',
        marker={'size': 1},
    )
])
fig.write_html('plot_sentiment.html')

In [38]:
fig.show()

See the attached HTML file to explore the plot. When exporting Plotly usually does not work anymore.

## Let's test it out...

First we create the input sequence that we want to run the model against.

In [72]:
testing = [word_to_id[word] for word in ['worst', 'movie', 'ever']]

In [73]:
testing

[249, 20, 126]

Let's run the encoder and see where our sequence falls in the latent space.

In [74]:
testing_space = encoder.predict(np.array([testing]))

In [75]:
testing_space

array([[12.723447 ,  5.9130907,  2.3925514]], dtype=float32)

We can use the euclidean distance to figure out which dataset in the latent space is closest to what we just used as an input sequence. After we sort the array by its distances we should see the closest ones appear at the top:

In [76]:
full_distances = euclidean_distances(np.array([testing_space[0]]), enc)

In [77]:
distances = np.stack(
    [
        full_distances.reshape(25000, 1),
        np.array([[it] for it in range(25000)]),
    ],
    axis=1
).reshape(25000, 2).tolist()
distances = sorted(distances, key=lambda x: x[0])

In [78]:
distances[:10]

[[1.980453362193657e-06, 4725.0],
 [1.980453362193657e-06, 6223.0],
 [1.980453362193657e-06, 7100.0],
 [1.980453362193657e-06, 8548.0],
 [1.980453362193657e-06, 9516.0],
 [1.980453362193657e-06, 11159.0],
 [1.980453362193657e-06, 15366.0],
 [1.980453362193657e-06, 22165.0],
 [0.6566333770751953, 17013.0],
 [0.7564414739608765, 16562.0]]

Now we can display all the queries that the model encoded as "similar" to our input query.

In [79]:
for dist, key in distances[:20]:
    key = int(key)
    print(key, dist, [id_to_word[idx] for idx in x_train[key]])

4725 1.980453362193657e-06 ['worst', 'movie', 'ever']
6223 1.980453362193657e-06 ['worst', 'movie', 'ever']
7100 1.980453362193657e-06 ['worst', 'movie', 'ever']
8548 1.980453362193657e-06 ['worst', 'movie', 'ever']
9516 1.980453362193657e-06 ['worst', 'movie', 'ever']
11159 1.980453362193657e-06 ['worst', 'movie', 'ever']
15366 1.980453362193657e-06 ['worst', 'movie', 'ever']
22165 1.980453362193657e-06 ['worst', 'movie', 'ever']
17013 0.6566333770751953 ['those', 'three', 'together']
16562 0.7564414739608765 ['any', 'film', 'before']
1196 0.8630278706550598 ['worst', 'movies', 'ever']
19536 0.8630278706550598 ['worst', 'movies', 'ever']
10394 0.8974630236625671 ['bad', 'horror', 'film']
13034 0.972442626953125 ['scary', 'horror', 'film']
8550 1.0928292274475098 ['big', 'well', 'done']
621 1.2364046573638916 ['re', 'write', 'history']
21244 1.393841028213501 ['his', 'lost', 'career']
6507 1.472649097442627 ['great', 'family', 'film']
5782 1.4924644231796265 ['other', 'then', 'entertai